In [11]:
import numpy as np
import os
import time
import datetime
import threading
import pandas as pd
import pickle
from mediapipe.python.solutions import drawing_utils as mp_drawing
from mediapipe.python.solutions import pose as mp_pose
import matplotlib.pyplot as plt
import cv2
import mediapipe as mp
from typing import Mapping
mp_pose = mp.solutions.pose

from audSample import *
from createAudio import *

In [12]:
classifier = pickle.load(open('yoga_model/latest_model1', 'rb'))

In [13]:
# to calculate angle in three points
def getAngles(item, pt1, pt2, pt3):
    a = item[pt1]
    b = item[pt2]
    c = item[pt3]
    ba = a - b
    bc = c - b
    cosine_angle = np.dot(ba, bc) / (np.linalg.norm(ba) * np.linalg.norm(bc))
    angle = (np.arccos(cosine_angle))*(180/np.pi)
    return angle

In [14]:
def chk_vis(lis):
    cnt = 0
    for obj in lis:
        print(obj.visibility)
        if (obj.visibility>0.05): cnt+=1
    if (cnt==33): return True
    else: return False 

In [15]:

from timeit import default_timer as timer

PosesAudioLoc = "audioFiles/poses/"
SecAudioLoc = "audioFiles/seconds/"


In [16]:
import json
colr = 255
with open("pose_angle.json", "r") as pose_angle:
    pose_data = json.load(pose_angle)
def chck_angle(ps_name, angle_dic):
    angle_col_dic = {}
    for d_angle in pose_data[ps_name]:
        mn, std = pose_data[ps_name][d_angle]
        rat = abs(mn-angle_dic[d_angle])/mn
        if rat>1: rat = 1
        angle_col_dic[d_angle] = (0, colr*(1-rat), colr*rat)
    # print(angle_col_dic)
    return angle_col_dic
# print(pose_data)    

In [17]:
recently = []
steady_time = []
def start_vid(frame_rate):
    secCheck = 0
    vid = cv2.VideoCapture(0)
    # frame_rate = 30
    prev = time.time()
    threadChk = 0
    while(True):
        
        # Capture the video frame
        # by frame
        time_elapsed = time.time() - prev
        ret, frame = vid.read()
        # time_elapsed = time.time() - prev
        # ret, frame = self.video.read()
        if time_elapsed > 1./frame_rate:
            prev = time.time()
            frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            with mp_pose.Pose() as pose_tracker:
                result = pose_tracker.process(image=frame)
                # mp_drawing.plot_landmarks(results.pose_world_landmarks, mp_pose.POSE_CONNECTIONS)
                pose_landmarks = result.pose_landmarks
            output_frame = frame.copy()
            # print(pose_landmarks.landmark)
            pose_name = ""
            if pose_landmarks is not None:
                dict_obj = {}
                for i in range(0,33):
                    dict_obj[i] = mp_drawing.DrawingSpec(color=mp_drawing.WHITE_COLOR)
                pose_landmarka = [[lmk.x, lmk.y, lmk.z] for lmk in pose_landmarks.landmark]
                output_frame = cv2.cvtColor(output_frame, cv2.COLOR_RGB2BGR)
                frame_height, frame_width = frame.shape[:2]
                pose_landmarka *= np.array([frame_width, frame_height, frame_width])
                # uncomment this when predicting
                item = pose_landmarka
                angle_dict = {
                    'left_shoulder': getAngles(item, 13, 11, 12),
                    'right_shoulder': getAngles(item, 24, 12, 14),
                    'left_elbow': getAngles(item, 15, 13, 11),
                    'right_elbow': getAngles(item, 12, 14, 16),
                    'left_leg_waist': getAngles(item, 11, 23, 25),
                    'right_leg_waist': getAngles(item, 12, 24, 26),
                    'left_knee': getAngles(item, 23, 25, 27),
                    'right_knee': getAngles(item, 24, 26, 28),
                }
                arr = np.array([angle_dict['left_shoulder'],
                angle_dict['right_shoulder'],
                angle_dict['left_elbow'],
                angle_dict['right_elbow'],
                angle_dict['left_leg_waist'],
                angle_dict['right_leg_waist'],
                angle_dict['left_knee'],
                angle_dict['right_knee']])
                res = classifier.predict([arr]) # classified pose name
                pose_name = res[0]
                angle_colr = chck_angle(pose_name, angle_dict)
                dict_obj[11] = mp_drawing.DrawingSpec(color=angle_colr["left_shoulder"])
                dict_obj[12] = mp_drawing.DrawingSpec(color=angle_colr["right_shoulder"])
                dict_obj[13] = mp_drawing.DrawingSpec(color=angle_colr["left_elbow"])
                dict_obj[14] = mp_drawing.DrawingSpec(color=angle_colr["right_elbow"])
                dict_obj[23] = mp_drawing.DrawingSpec(color=angle_colr["left_leg_waist"])
                dict_obj[24] = mp_drawing.DrawingSpec(color=angle_colr["right_leg_waist"])
                dict_obj[25] = mp_drawing.DrawingSpec(color=angle_colr["left_knee"])
                dict_obj[26] = mp_drawing.DrawingSpec(color=angle_colr["right_knee"])
                x: Mapping[int, mp_drawing.DrawingSpec] = dict_obj
                mp_drawing.draw_landmarks(
                    image=output_frame,
                    landmark_list=pose_landmarks,
                    connections=mp_pose.POSE_CONNECTIONS,
                    landmark_drawing_spec=  x)
                assert len(pose_landmarks.landmark) == 33, 'Unexpected number of predicted pose landmarks: {}'.format(len(pose_landmarks.landmark))
                # if chk_vis(pose_landmarks.landmark):
                # for i in pose_landmarks.landmark:
                #     print(i)
            cv2.rectangle(output_frame, (0,0), (650, 50), (0,0,0), -1)
            output_frame = cv2.putText(output_frame, pose_name, (50,50), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 0, 255), 2, cv2.LINE_AA)
            # cv2.imshow('frame', output_frame)
            c_time = timer()
            
            ideal=1
            for i in angle_colr.values():
                if i[2] > 150: ideal = 0  # if red detected clear the timer

            if pose_name != "" and ideal:
                
                if ideal:
                    steady_time_now = timer()
                    steadyF = 0
                    if not steady_time:
                        steady_time.append(steady_time_now)
                    elif (steady_time_now - steady_time[0])>3:
                        steadyF = 1
                    else:
                        # print(steady_time_now-steady_time[0])
                        steady_time.append(steady_time_now)
                        
                    output_frame = cv2.putText(output_frame, str("{:.0f}".format(steady_time_now-steady_time[0]))+" s", (300,30), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA)
                    if steadyF == 1:
                        countSay = "{:.0f}".format(steady_time_now-steady_time[0])
                        print(angle_colr)
                        if not recently: # classify and say
                            t1 = threading.Thread(target=start_playlist, args=[[ f"{PosesAudioLoc}{pose_name}.wav"]])
                            t1.start()
                            threadChk = 1
                            recently.append(c_time)

                        elif secCheck==0:
                            if int(countSay)%15 == 0:
                                print(countSay)
                                t1 = threading.Thread(target=start_playlist, args=[[ f"{SecAudioLoc}{countSay}sec.wav"]])
                                t1.start()
                                recently.pop()
                                recently.append(c_time)
                                secCheck = 1
                            else:
                                secCheck = 0
                        
                        if secCheck==1 and int(countSay)%15 != 0: secCheck=0
                    
                    
            else:
                steady_time.clear()
                recently.clear()
            cv2.imshow('frame', output_frame)
        # the 'q' button is set as the
        # quitting button you may use any
        # desired button of your choice
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break


    if threadChk: t1.join()
    # After the loop release the cap object
    vid.release()
    # Destroy all the windows
    cv2.destroyAllWindows()

In [18]:
classifier.classes_

array(['adho mukha savanasana', 'ashtanga namaskar', 'aswa sanchalnasan',
       'bhujangasana', 'pranamasan', 'urdhva hastasana', 'uttanasana'],
      dtype=object)

In [19]:
# classifier.metric_params()

In [20]:
import warnings
warnings.filterwarnings('ignore')
start_vid(10)

x: 0.6260396242141724
y: 0.45472824573516846
z: -1.3923662900924683
visibility: 0.9996193647384644

x: 0.6374222040176392
y: 0.3616374731063843
z: -1.3142046928405762
visibility: 0.9995043277740479

x: 0.6538203954696655
y: 0.35732269287109375
z: -1.3144268989562988
visibility: 0.9994206428527832

x: 0.6683785319328308
y: 0.3544327914714813
z: -1.31512451171875
visibility: 0.9994179010391235

x: 0.5783761143684387
y: 0.3714855909347534
z: -1.3284977674484253
visibility: 0.9994797110557556

x: 0.556260883808136
y: 0.37296438217163086
z: -1.3283153772354126
visibility: 0.9994683861732483

x: 0.53470778465271
y: 0.37473079562187195
z: -1.3288146257400513
visibility: 0.9995177984237671

x: 0.6730950474739075
y: 0.37663519382476807
z: -0.700917661190033
visibility: 0.9995425939559937

x: 0.4988733232021332
y: 0.3932831585407257
z: -0.7412745952606201
visibility: 0.9996446371078491

x: 0.6573318243026733
y: 0.5170196294784546
z: -1.15827476978302
visibility: 0.9998111128807068

x: 0.58548116

Exception in thread Thread-5:
Traceback (most recent call last):
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "d:\sem 7\mini-project\project\YogaPoseDetect\audSample.py", line 17, in start_playlist
    pygame.mixer.music.load(playList[0])
pygame.error: No file 'audioFiles/poses/ashtanga namaskar.wav' found in working directory 'd:\sem 7\mini-project\project\YogaPoseDetect'.


x: 0.5607410073280334
y: 0.4448930025100708
z: -1.2224783897399902
visibility: 0.9997326731681824

x: 0.5828612446784973
y: 0.35594356060028076
z: -1.155189037322998
visibility: 0.9996405839920044

x: 0.6014874577522278
y: 0.35257863998413086
z: -1.1551860570907593
visibility: 0.9994627833366394

x: 0.6190258860588074
y: 0.350566029548645
z: -1.15590238571167
visibility: 0.9996187686920166

x: 0.5333411693572998
y: 0.36711379885673523
z: -1.1398378610610962
visibility: 0.9994283318519592

x: 0.5188851356506348
y: 0.3706684112548828
z: -1.13937509059906
visibility: 0.9991589784622192

x: 0.5049645900726318
y: 0.3748542070388794
z: -1.1396706104278564
visibility: 0.9993982315063477

x: 0.6430648565292358
y: 0.3795682191848755
z: -0.6625041365623474
visibility: 0.9996956586837769

x: 0.49983349442481995
y: 0.4033322334289551
z: -0.5606635212898254
visibility: 0.999269425868988

x: 0.6034006476402283
y: 0.515200138092041
z: -1.0390266180038452
visibility: 0.999842643737793

x: 0.5404707193

Exception in thread Thread-6:
Traceback (most recent call last):
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "d:\sem 7\mini-project\project\YogaPoseDetect\audSample.py", line 17, in start_playlist
    pygame.mixer.music.load(playList[0])
pygame.error: No file 'audioFiles/poses/ashtanga namaskar.wav' found in working directory 'd:\sem 7\mini-project\project\YogaPoseDetect'.


x: 0.5281292796134949
y: 0.41294002532958984
z: -1.4101921319961548
visibility: 0.9998693466186523

x: 0.5494652986526489
y: 0.3198155164718628
z: -1.3470426797866821
visibility: 0.9998257756233215

x: 0.5737980604171753
y: 0.31571531295776367
z: -1.347147822380066
visibility: 0.9998235106468201

x: 0.5966381430625916
y: 0.3124392330646515
z: -1.3478832244873047
visibility: 0.9998210072517395

x: 0.489525705575943
y: 0.33021095395088196
z: -1.3328042030334473
visibility: 0.9997695088386536

x: 0.4727856516838074
y: 0.33286476135253906
z: -1.332594633102417
visibility: 0.9997585415840149

x: 0.45625290274620056
y: 0.3357257843017578
z: -1.3329583406448364
visibility: 0.9997338652610779

x: 0.6328777074813843
y: 0.3418532609939575
z: -0.7794507741928101
visibility: 0.9998809099197388

x: 0.4543018937110901
y: 0.37081849575042725
z: -0.6886317133903503
visibility: 0.9998061060905457

x: 0.5904018878936768
y: 0.4853428602218628
z: -1.1924477815628052
visibility: 0.9999481439590454

x: 0.50

...

x: 0.31781095266342163
y: 0.3730466663837433
z: -0.10101892799139023
visibility: 0.9993866682052612

x: 0.32310202717781067
y: 0.3582943081855774
z: -0.08118633180856705
visibility: 0.9989357590675354

x: 0.325349360704422
y: 0.35821008682250977
z: -0.08123272657394409
visibility: 0.9988535642623901

x: 0.3282897174358368
y: 0.3580476939678192
z: -0.08130092173814774
visibility: 0.9988942742347717

x: 0.3119225800037384
y: 0.3587099015712738
z: -0.07981419563293457
visibility: 0.9986701011657715

x: 0.3070189356803894
y: 0.3586861193180084
z: -0.07979635149240494
visibility: 0.9984803795814514

x: 0.30260831117630005
y: 0.3588462769985199
z: -0.07979495823383331
visibility: 0.9988335967063904

x: 0.33312124013900757
y: 0.3639799952507019
z: 0.034923311322927475
visibility: 0.9988318085670471

x: 0.29739901423454285
y: 0.3641735017299652
z: 0.04254749417304993
visibility: 0.9983996748924255

x: 0.3247149884700775
y: 0.38754189014434814
z: -0.056168120354413986
visibility: 0.999212503433

Exception in thread Thread-18:
Traceback (most recent call last):
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "d:\sem 7\mini-project\project\YogaPoseDetect\audSample.py", line 17, in start_playlist
    pygame.mixer.music.load(playList[0])
pygame.error: No file 'audioFiles/poses/pranamasan.wav' found in working directory 'd:\sem 7\mini-project\project\YogaPoseDetect'.


x: 0.2546330392360687
y: 0.5339953899383545
z: -0.2106204330921173
visibility: 0.999742329120636

x: 0.26341816782951355
y: 0.5164664387702942
z: -0.1935318410396576
visibility: 0.9996988773345947

x: 0.26779407262802124
y: 0.5156964063644409
z: -0.19345614314079285
visibility: 0.9995710253715515

x: 0.2716565430164337
y: 0.5151822566986084
z: -0.1933506429195404
visibility: 0.9996970891952515

x: 0.24679675698280334
y: 0.5172691345214844
z: -0.19097182154655457
visibility: 0.9997350573539734

x: 0.2409503012895584
y: 0.5169833898544312
z: -0.19086779654026031
visibility: 0.9996196031570435

x: 0.23632459342479706
y: 0.5169287919998169
z: -0.190962553024292
visibility: 0.9997586607933044

x: 0.2807694375514984
y: 0.5212594270706177
z: -0.07908130437135696
visibility: 0.999529242515564

x: 0.23004193603992462
y: 0.5238125324249268
z: -0.06185685843229294
visibility: 0.9996474981307983

x: 0.2657696604728699
y: 0.5552782416343689
z: -0.1687886267900467
visibility: 0.9998099207878113

x: 

Exception in thread Thread-19:
Traceback (most recent call last):
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "c:\users\prathmesh waghmode\appdata\local\programs\python\python38\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "d:\sem 7\mini-project\project\YogaPoseDetect\audSample.py", line 17, in start_playlist
    pygame.mixer.music.load(playList[0])
pygame.error: No file 'audioFiles/poses/ashtanga namaskar.wav' found in working directory 'd:\sem 7\mini-project\project\YogaPoseDetect'.


x: 0.30347156524658203
y: 0.5417625904083252
z: -0.22120828926563263
visibility: 0.9995635151863098

x: 0.3119874894618988
y: 0.5226030349731445
z: -0.20443126559257507
visibility: 0.999508261680603

x: 0.3159925937652588
y: 0.5222840309143066
z: -0.20438244938850403
visibility: 0.9993222951889038

x: 0.320697546005249
y: 0.5218086838722229
z: -0.2042846381664276
visibility: 0.9994874000549316

x: 0.2953107953071594
y: 0.523044764995575
z: -0.20343728363513947
visibility: 0.9995713829994202

x: 0.2890279293060303
y: 0.5227862596511841
z: -0.20338329672813416
visibility: 0.999413013458252

x: 0.2841491401195526
y: 0.5225698351860046
z: -0.20350022614002228
visibility: 0.9996019005775452

x: 0.32790064811706543
y: 0.5279595851898193
z: -0.08910124748945236
visibility: 0.9992502331733704

x: 0.27772197127342224
y: 0.5285152196884155
z: -0.07858055830001831
visibility: 0.9994634985923767

x: 0.31300705671310425
y: 0.5633598566055298
z: -0.17803186178207397
visibility: 0.9996962547302246

x